# Interpretability: Understanding Predictions Using Car Data

## Overview

This notebook provides an overview of applying Howso Engine to make predictions based on historical data and harnessing Howso Engine’s interpretability capabilities to understand why the predictions were made. Here, we demonstrate these capabilities on vehicle data. We train Howso Engine to predict classes of vehicles, understand potential anomalies, investigate vehicles on a case-by-case basis, and review the data that contributed to the predictions. This is a straightforward example of the power of Howso Engine to gain insights from data. 

## Recipe Goals

This recipe hopes to serve as a use-case driven example of how to use the Howso Engine's interpretability tools to further understand how predictions are derived and what influences them the most.

In [1]:
import pandas as pd
from sklearn.metrics import (
    accuracy_score,
    f1_score,
)

from howso import engine
from howso.utilities import infer_feature_attributes
from howso.visuals import plot_dataset

# Section 1: Model Training and Evaluation

## Step 1: Load Data

Our dataset here is a collection of records describing models of various vehicle models across the last few decades. The data consists of 10 features describing some common properties of each car model.

The last column, vehicle class, is our target variable. We'll use the other variables (with the exception of make and model, as this would be too easy) to build a model. 

In [2]:
df = pd.read_csv('../../../data/vehicle_processed.csv')

# drop any duplicate records
df = df.drop_duplicates()

# keep a copy of the original data for later reference Make & Model
df_original = df.copy()

df = df.drop(['Make', 'Model'], axis=1)
df

CityMPG                   DriveType FuelType  HighwayMPG  Year  \
0           23           Front-Wheel Drive  Regular          33  1985   
1           17  4-Wheel or All-Wheel Drive  Premium          23  1993   
2           21           Front-Wheel Drive  Regular          24  1993   
3           22           Front-Wheel Drive  Regular          29  1993   
4           23           Front-Wheel Drive  Regular          26  1993   
...        ...                         ...      ...         ...   ...   
23600       21           Front-Wheel Drive  Regular          32  1993   
23601       19           Front-Wheel Drive  Regular          26  1993   
23602       20           Front-Wheel Drive  Regular          28  1993   
23603       18  4-Wheel or All-Wheel Drive  Regular          24  1993   
23605       16  4-Wheel or All-Wheel Drive  Premium          21  1993   

       PassengerVolume  LuggageVolume     VehicleClass  
0                   77             19  Subcompact Cars  
1                   90             14     Compact Cars  
2                   88             15     Compact Cars  
3                   88             15     Compact Cars  
4                   89             13     Compact Cars  
...                ...            ...              ...  
23600               89             12     Compact Cars  
23601               90             14     Compact Cars  
23602               90             14     Compact Cars  
23603               90             14     Compact Cars  
23605               90             14     Compact Cars  

[21998 rows x 8 columns]

> NOTE: The Howso Engine handles missing data quite well natively. This dataset actually contains more than a few missing values in the "DriveType" feature, see below.

In [3]:
df.isnull().sum()

CityMPG              0
DriveType          783
FuelType             0
HighwayMPG           0
Year                 0
PassengerVolume      0
LuggageVolume        0
VehicleClass         0
dtype: int64

In [4]:
df[df.DriveType.isnull()]

CityMPG DriveType FuelType  HighwayMPG  Year  PassengerVolume  \
9707        15       NaN  Regular          20  1984               50   
9708        16       NaN  Regular          20  1984               50   
9709        16       NaN  Regular          22  1984               50   
9710        18       NaN  Regular          24  1984               50   
9711        17       NaN  Regular          24  1984               74   
...        ...       ...      ...         ...   ...              ...   
10848       14       NaN  Regular          19  1984              110   
10849       13       NaN  Regular          19  1984              112   
10850       13       NaN  Regular          19  1984              112   
10851       13       NaN  Regular          20  1984              110   
10852       14       NaN  Regular          19  1984              110   

       LuggageVolume                  VehicleClass  
9707              22                   Two Seaters  
9708              22                   Two Seaters  
9709              22                   Two Seaters  
9710              22                   Two Seaters  
9711               7              Minicompact Cars  
...              ...                           ...  
10848             50  Midsize-Large Station Wagons  
10849             53  Midsize-Large Station Wagons  
10850             53  Midsize-Large Station Wagons  
10851             50  Midsize-Large Station Wagons  
10852             50  Midsize-Large Station Wagons  

[783 rows x 8 columns]

Below we also display the different values seen in the data for our desired target feature, "VehicleClass".

In [5]:
labels = df['VehicleClass'].unique()
list(labels)

['Subcompact Cars',
 'Compact Cars',
 'Midsize Cars',
 'Large Cars',
 'Small Station Wagons',
 'Midsize-Large Station Wagons',
 'Minicompact Cars',
 'Two Seaters',
 'Midsize Station Wagons',
 'Special Purpose Vehicle 4WD',
 'Sport Utility Vehicle - 4WD',
 'Sport Utility Vehicle - 2WD',
 'Small Pickup Trucks 4WD',
 'Small Sport Utility Vehicle 4WD',
 'Small Sport Utility Vehicle 2WD',
 'Special Purpose Vehicle 2WD',
 'Standard Sport Utility Vehicle 2WD',
 'Standard Sport Utility Vehicle 4WD']

## Step 2: Train and Analyze

For the purpose of this demo we will use the data of cars made before 2021 to make predictions on data representing cars made in 2021.

In [6]:
test_index = df[df['Year'].isin([2021])].index
train_index = df[~df['Year'].isin([2021])].index

print("train size (ratio): " + str(round(len(train_index) / df.shape[0], 2) ))
print("test size (ratio): " + str(round(len(test_index) / df.shape[0], 2) ) )

train size (ratio): 0.97
test size (ratio): 0.03


In [7]:
df_train = df.loc[train_index, :]
X_test = df.loc[test_index, :].drop('VehicleClass', axis=1)
y_test = df.loc[test_index, 'VehicleClass']

As mentioned in other recipes, we strongly encourage users to always inspect the feature attributes returned by `infer_feature_attributes`. This function uses some heuristics to attempt to infer feature types and other attributes, but an incorrect assumption can drastically impact the performance of the Trainee and give undesired results.

Additionally, users should not be afraid to manually alter the feature attributes, especially for attributes such as "type" or "bounds".

In [8]:
# Explicitly specify continuous features
custom_features = {}

cont_features = ['CityMPG', 'HighwayMPG', 'PassengerVolume', 'LuggageVolume', 'Year']
types = {'continuous': cont_features}

# Infer feature attributes, with a dictionary where types for continuous feature
# are pre-defined
features = infer_feature_attributes(df, types=types)

features.to_dataframe()

type decimal_places  bounds                     \
                                               min     max allow_null   
CityMPG          continuous            0.0     0.0   243.0      False   
DriveType           nominal            NaN     NaN     NaN       True   
FuelType            nominal            NaN     NaN     NaN       True   
HighwayMPG       continuous            0.0     0.0   213.0      False   
Year             continuous            0.0  1959.0  2047.0      False   
PassengerVolume  continuous            0.0     0.0   321.0      False   
LuggageVolume    continuous            0.0     0.0    90.0      False   
VehicleClass        nominal            NaN     NaN     NaN       True   

                                          data_type original_type       
                observed_min observed_max               data_type size  
CityMPG                  6.0        150.0    number       integer  8.0  
DriveType                NaN          NaN    string        string  NaN  
FuelType                 NaN          NaN    string        string  NaN  
HighwayMPG               9.0        133.0    number       integer  8.0  
Year                  1984.0       2022.0    number       integer  8.0  
PassengerVolume          1.0        195.0    number       integer  8.0  
LuggageVolume            1.0         55.0    number       integer  8.0  
VehicleClass             NaN          NaN    string        string  NaN

In [9]:
# Specify context and action features
context_features = features.get_names(without=['VehicleClass'])
action_features = ['VehicleClass']

# Initialize the Trainee, train it, and analyze the data
t = engine.Trainee(name='Engine - Car Type Recipe',
                    features=features,
                    overwrite_existing=True)

t.train(df_train)

t.analyze()

## Step 3: Predict on the Test Set

Now let's see how well the Trainee can predict "VehicleClass" of the test data. Let's inspect both accuracy and F1 score for each class.

In [10]:
results = t.react(X_test, action_features=action_features, context_features=context_features)
predictions = results['action']['VehicleClass']

In [11]:
accuracy = round(accuracy_score(y_test, predictions), 3)
print("Accuracy: " +  str(accuracy))
print("=" * 30)


print("Per-Class F1 Scores:\n")
score = f1_score(y_test, predictions, average=None)
for i in range(0, len(set(y_test))):
    print(labels[i] + ': ' + str(round(score[i], 3)))

Accuracy: 0.958
Per-Class F1 Scores:

Subcompact Cars: 0.969
Compact Cars: 0.948
Midsize Cars: 0.965
Large Cars: 0.957
Small Station Wagons: 0.986
Midsize-Large Station Wagons: 1.0
Minicompact Cars: 0.833
Two Seaters: 0.868
Midsize Station Wagons: 1.0
Special Purpose Vehicle 4WD: 1.0
Sport Utility Vehicle - 4WD: 0.966


We see we have satisfactory F1 scores for most of the classes, but there are one or two that fall a bit behind. Let's check if those classes are well represented in the training data. 

In [12]:
df_train['VehicleClass'].value_counts()

VehicleClass
Compact Cars                          5511
Subcompact Cars                       4743
Midsize Cars                          4678
Large Cars                            2152
Small Station Wagons                  1474
Minicompact Cars                      1294
Midsize-Large Station Wagons           590
Midsize Station Wagons                 475
Two Seaters                            157
Sport Utility Vehicle - 4WD            135
Small Sport Utility Vehicle 2WD         90
Small Sport Utility Vehicle 4WD         50
Sport Utility Vehicle - 2WD             50
Standard Sport Utility Vehicle 4WD      15
Special Purpose Vehicle 2WD              6
Standard Sport Utility Vehicle 2WD       5
Special Purpose Vehicle 4WD              3
Small Pickup Trucks 4WD                  1
Name: count, dtype: int64

Unsurprisingly, it looks like the class with the lowest F1 score among the test set predictions is one of the classes with the least training data. This should ease our concerns for now. Let's move on.

# Section 2: Leveraging Interpretability

## Step 1: Identifying Anomalous Cases

One way to investigate your data is to identify the most anomalous cases in the dataset. The Howso Engine allows users to do this easily in many ways. Here we demonstrate how to calculate the "Familiarity Conviction (Addition)" for every case in the model then display those cases that have both the highest and lowest values.

> Reminder: All forms of Conviction in the Howso Engine are a ratio of expected surprisal to observed surprisal with a range of (0, inf). Knowing this, a conviction value of 1.0 indicates that the case presents the expected level of surprisal. Furthemore, this means that both low values (< 1.0) and high values (> 1.0) indicate a deviation from the expected level of surprisal. It isn't straightforward to define a threshold of conviction that indicates a "true" anomaly, we recommend tuning thresholds like this on a per-dataset basis. However, it usually a safe bet to regard cases with the lowest and highest conviction values to be the most anomalous.

In [13]:
# react_into_features computes the specified values and caches them into every case of the model as a feature
t.react_into_features(familiarity_conviction_addition=True)
stored_convictions = t.get_cases(session=t.active_session, features=['familiarity_conviction_addition','.session_training_index', '.session'])

In [14]:
convict_df = df_original.loc[train_index].reset_index(drop=True).join(stored_convictions).rename(columns={'familiarity_conviction_addition':'convictions'})
print("The cases with the lowest Familiarity Convictions:")
convict_df.sort_values('convictions').head()

The cases with the lowest Familiarity Convictions:


CityMPG                   DriveType     FuelType  HighwayMPG  \
1085        13            Rear-Wheel Drive      Regular          17   
12433      138           Front-Wheel Drive  Electricity         105   
9549        18  4-Wheel or All-Wheel Drive      Regular          20   
11726      107            Rear-Wheel Drive  Electricity          96   
9302        12                         NaN      Regular          17   

                                Make     Model  Year  PassengerVolume  \
1085                   Federal Coach       85J  1995              176   
12433                          Scion     iQ EV  2013               73   
9549   Import Foreign Auto Sales Inc  1fas 410  1984               28   
11726                            BMW  Active E  2011               86   
9302          Bitter Gmbh and Co. Kg        SC  1984                1   

       LuggageVolume             VehicleClass  convictions  \
1085               1               Large Cars     0.006235   
12433              4         Minicompact Cars     0.016400   
9549               9  Small Pickup Trucks 4WD     0.018486   
11726              6          Subcompact Cars     0.019114   
9302              16             Midsize Cars     0.019485   

       .session_training_index                              .session  
1085                      1085  4256ce17-56fc-418b-9980-8146c8751a64  
12433                    12433  4256ce17-56fc-418b-9980-8146c8751a64  
9549                      9549  4256ce17-56fc-418b-9980-8146c8751a64  
11726                    11726  4256ce17-56fc-418b-9980-8146c8751a64  
9302                      9302  4256ce17-56fc-418b-9980-8146c8751a64

In [15]:
print("The cases with the highest Familiarity Convictions:")
convict_df.sort_values('convictions', ascending=False).head()

The cases with the highest Familiarity Convictions:


CityMPG          DriveType         FuelType  HighwayMPG        Make  \
470         21  Front-Wheel Drive          Regular          32  Oldsmobile   
12522       15  Front-Wheel Drive          Regular          23       Dodge   
10294       19  Front-Wheel Drive          Regular          30       Buick   
11182       24  Front-Wheel Drive          Regular          35       Buick   
3504        17  Front-Wheel Drive  Gasoline or E85          25        Ford   

                  Model  Year  PassengerVolume  LuggageVolume  \
470             Achieva  1994               90             14   
12522            Shadow  1987               89             13   
10294   Lacrosse/Allure  2010              100             16   
11182  LaCrosse eAssist  2012              100             16   
3504       Taurus Wagon  2000              104             39   

                 VehicleClass  convictions  .session_training_index  \
470              Compact Cars  1214.588928                      470   
12522            Compact Cars   602.766023                    12522   
10294            Midsize Cars   602.156516                    10294   
11182            Midsize Cars   362.824054                    11182   
3504   Midsize Station Wagons   281.716489                     3504   

                                   .session  
470    4256ce17-56fc-418b-9980-8146c8751a64  
12522  4256ce17-56fc-418b-9980-8146c8751a64  
10294  4256ce17-56fc-418b-9980-8146c8751a64  
11182  4256ce17-56fc-418b-9980-8146c8751a64  
3504   4256ce17-56fc-418b-9980-8146c8751a64

## Step 2. Investigate a Single Prediction

To gain insight into the Trainee's predictions, we will take a single case representing the Kia K900 and make a prediction on it. In our call to `react`, we will also specify some additional requested information with the `details` parameter that will provide us with some interpretability tools to help understand how the Trainee came to it's prediction.

First we display ths case below, so we know about the case we are discussing. Notably, we see its "VehicleClass" is "Large Cars" which is our action feature.

In [45]:
# Investigate the Kia K900 as an example
k900 = convict_df[(convict_df.Model=='K900') & (convict_df.Year==2015)].iloc[0, :]
k900_case_indices = [(k900['.session'], k900['.session_training_index'])]
k900

CityMPG                                                      18
DriveType                                      Rear-Wheel Drive
FuelType                                                Regular
HighwayMPG                                                   26
Make                                                        Kia
Model                                                      K900
Year                                                       2015
PassengerVolume                                             110
LuggageVolume                                                16
VehicleClass                                         Large Cars
convictions                                            1.954657
.session_training_index                                   13336
.session                   4256ce17-56fc-418b-9980-8146c8751a64
Name: 13336, dtype: object

<img src="../../../data/K900_overview.png" width="320">

Howso Engine's power is in its interpretability. Let's see what the model can tell us about this car.

In [46]:
# Specify all the desired details, which will augment the return value of react
# to include additional information
details = {'most_similar_cases': True,
           'num_most_similar_cases': 30,
           'boundary_cases': True,
           'num_boundary_cases': 30,
           'influential_cases': True,
           'feature_robust_accuracy_contributions': True,
           'feature_full_residuals': True}

new_result = t.react(case_indices=k900_case_indices,
                     action_features=action_features,
                     preserve_feature_values=context_features,
                     leave_case_out=True, details=details)

Let's also see where our Kia K900 stands among the other data. To do this, we show a scatterplot with axes of "LuggageVolume" and "PassengerVolume". Here the colors indicate the "VehicleClass". With these colors, we can see that the Kia K900 lies between many other "Large Cars" in terms of these two features, we can reasonably estimate that this case will get the correct predicted value.

In [47]:
plot_dataset(
    convict_df, "LuggageVolume", "PassengerVolume",
    highlight_selection_conditions={"Make": "Kia", "Model": "K900", "Year": 2015},
    highlight_label="Kia K900",
    alpha=0.3,
    hue="VehicleClass",
    size="convictions",
)

To check if we got the correct predicted value for "VehicleClass" we can check the "action" key of the dictionary returned from `react`.

In [48]:
new_result['action']['VehicleClass'][0]

'Large Cars'

So we see we got the correct prediction from the Trainee. But what played into that decision?

Below we show all of the different "details" that were returned in the `react` response. These details are what will provide us with in-depth interpretability information to further understand how the prediction was made.

In [49]:
list(new_result['details'].keys())

['feature_full_residuals',
 'feature_robust_accuracy_contributions',
 'influential_cases',
 'action_features',
 'most_similar_cases',
 'boundary_cases']

There is a LOT of information here, a few interesting bits:

1. Most similar cases: These cases most similar to the K900 we predicted according to the Howso Engine.
2. Boundary cases: These are the cases most similar to the case we predicted in terms of context features, but with differing values for the action feature(s).

## Step 3: Inspect the Similar cases and Boundary cases

First let's look at the most similar cases. In this list of similar cases, we see some other versions of the K900 and the Hyundai Genesis.

Conveniently, if we do some research, we can find that the K900 is "a derivative of the Hyundai Equus and Genesis". So we see that the origin of the K900 falls right inline with what we see in the data.

In [21]:
most_similar_df = new_result['details']['influential_cases'][0].drop('VehicleClass', axis=1)

most_similar_records = pd.merge(most_similar_df, df_original, on=context_features, how='left')

cols_order = ['.influence_weight', '.session', '.session_training_index', 'Make', 'Model', 'Year'] + most_similar_records.columns.drop(['.session_training_index', '.session', '.influence_weight', 'Make', 'Model', 'Year']).tolist()

most_similar_records = most_similar_records.loc[ : , cols_order]
most_similar_records.head(10)

.influence_weight                              .session  \
0           0.462731  4256ce17-56fc-418b-9980-8146c8751a64   
1           0.328305  4256ce17-56fc-418b-9980-8146c8751a64   
2           0.104475  4256ce17-56fc-418b-9980-8146c8751a64   
3           0.054464  4256ce17-56fc-418b-9980-8146c8751a64   
4           0.050025  4256ce17-56fc-418b-9980-8146c8751a64   

   .session_training_index     Make       Model  Year  LuggageVolume  \
0                    14482      Kia        K900  2016             16   
1                    13273  Hyundai     Genesis  2014             16   
2                    13676  Porsche  Panamera S  2015             16   
3                    15110      Kia        K900  2017             16   
4                    13673  Porsche    Panamera  2015             16   

          DriveType FuelType  PassengerVolume  CityMPG  HighwayMPG  \
0  Rear-Wheel Drive  Regular              110       17          25   
1  Rear-Wheel Drive  Regular              109       18          27   
2  Rear-Wheel Drive  Premium              108       18          26   
3  Rear-Wheel Drive  Regular              110       17          25   
4  Rear-Wheel Drive  Premium              108       18          28   

  VehicleClass  
0   Large Cars  
1   Large Cars  
2   Large Cars  
3   Large Cars  
4   Large Cars

<img src="../../../data/Firstgen_K9.png" width="1080">

Now let's look at the boundary cases.

Here we see a many cases that have very comparable "LuggageVolume", "HighwayMPG", and "PassengerVolume". Additionally, these cases also have the same "DriveType" and "VehicleClass". However, all of these classes are not "Large Cars" like the K900 we are discussing was predicted to be. This is the idea of boundary cases, they serve to help demonstrate to users what the most similar cases with a different action feature value look like. 

This can be used to help users see what context feature values may indicate a decision boundary.

In [22]:
boundary_case_df = new_result['details']['boundary_cases'][0].drop('VehicleClass', axis=1)

boundary_records = pd.merge(boundary_case_df, df_original, on=context_features, how='inner')

cols_order = ['.influence_weight', '.session', '.session_training_index', 'Make', 'Model', 'Year'] + boundary_records.columns.drop(['.session_training_index',  '.session', '.influence_weight', 'Make', 'Model', 'Year']).tolist()

boundary_records = boundary_records.loc[ : , cols_order]
boundary_records.head(10)

.influence_weight                              .session  \
0                  0  4256ce17-56fc-418b-9980-8146c8751a64   
1                  0  4256ce17-56fc-418b-9980-8146c8751a64   
2                  0  4256ce17-56fc-418b-9980-8146c8751a64   
3                  0  4256ce17-56fc-418b-9980-8146c8751a64   
4                  0  4256ce17-56fc-418b-9980-8146c8751a64   
5                  0  4256ce17-56fc-418b-9980-8146c8751a64   
6                  0  4256ce17-56fc-418b-9980-8146c8751a64   
7                  0  4256ce17-56fc-418b-9980-8146c8751a64   
8                  0  4256ce17-56fc-418b-9980-8146c8751a64   
9                  0  4256ce17-56fc-418b-9980-8146c8751a64   

   .session_training_index      Make       Model  Year  LuggageVolume  \
0                    10396  Infiniti         M37  2011             15   
1                    11105  Infiniti         M37  2012             15   
2                    11818  Infiniti        M37x  2013             15   
3                    11845  Infiniti         M37  2013             15   
4                    12377     Honda      Accord  2013             16   
5                    12683    Subaru  Legacy AWD  2014             15   
6                    13146     Honda      Accord  2014             16   
7                    13306  Infiniti         Q70  2014             15   
8                    13309  Infiniti         Q70  2014             15   
9                    13310  Infiniti     Q70 AWD  2014             15   

           DriveType FuelType  PassengerVolume  CityMPG  HighwayMPG  \
0   Rear-Wheel Drive  Premium              104       18          26   
1   Rear-Wheel Drive  Premium              104       18          26   
2    All-Wheel Drive  Premium              104       18          24   
3   Rear-Wheel Drive  Premium              104       18          26   
4  Front-Wheel Drive  Regular              103       18          28   
5    All-Wheel Drive  Regular              103       18          25   
6  Front-Wheel Drive  Regular              103       18          28   
7   Rear-Wheel Drive  Premium              104       16          24   
8   Rear-Wheel Drive  Premium              104       18          26   
9    All-Wheel Drive  Premium              104       17          24   

   VehicleClass  
0  Midsize Cars  
1  Midsize Cars  
2  Midsize Cars  
3  Midsize Cars  
4  Midsize Cars  
5  Midsize Cars  
6  Midsize Cars  
7  Midsize Cars  
8  Midsize Cars  
9  Midsize Cars

Notice how similar the boundary case are to the chosen example (Kia K900), with the exception of the 'VehicleClass'. Also, the ".influence_weight" is zero for all boundary cases which indicates the case of interest does not lie on the boundary.

Let's plot and identify the similar cases and boundary cases. Keep in mind we are only visualizing 2 of the 6 predictor variables. Therefore similar and boundary cases may not be right next to, or exactly on a class boundary, in the following plots.

In [23]:
plot_dataset(
    convict_df, "LuggageVolume", "PassengerVolume",
    highlight_selection_conditions={"Make": "Kia", "Model": "K900", "Year": 2015},
    highlight_label="Kia K900",
    alpha=0.3,
    hue="VehicleClass",
    size="convictions",
    most_similar_cases=most_similar_df,
    boundary_cases=boundary_case_df,
)

It's a bit difficult to see the similar cases in this plot as they are all very close to the K900 we are predicting. However we *can* see that the boundary cases are close, but not as close as the similar cases. Additionally, we see that the boundary cases are within a cluster of a different color, indicating their belonging to another class.

## Step 4. Inspect Feature Importance Metrics

First we can inspect the Mean Decrease in Accuracy for the local model around the prediction:

In [30]:
new_result['details']['feature_robust_accuracy_contributions']

LuggageVolume  DriveType      Year  FuelType  PassengerVolume   CityMPG  \
0       0.146755   0.019577  0.073264  0.045622         0.295013  0.070423   

   HighwayMPG  
0    0.068045

As observed from the 'most similar' and 'boundary' cases above, we can see that there were many vehicles which were similar to each other in that space. With the 'LuggageVolume' being a critical feature in distinguishing the VehicleClass in that region.
Higher values of MDA indicate that the feature is important for predicting the action feature.

> Note: MDA (Mean Decrease in Accuracy) measures are effectively an approximations of the SHAP value.

Another informative comparison is to check the local residuals against the global residuals to understand the uncertainty and predictability of the features in the area around the prediction in reference to those qualities of the model as a whole. 

In [34]:
feature_residuals = new_result["details"]["feature_full_residuals"]
feature_residuals.columns = feature_residuals.loc[0]
feature_residuals = feature_residuals.drop(0, axis=0)
print("Local Model Residuals")
feature_residuals

Local Model Residuals


Empty DataFrame
Columns: [0.37972941194299425, 0.4303608054281908, 1.2311656697409035, 1.6416069717631985, 0.4120698529721446, 4.6663555762949134e-05, 0.37323461101732675, 0.5997958248861593]
Index: []

In [40]:
t.react_aggregate(
    details = {
        "prediction_stats": True,
        "selected_prediction_stats": ["mae"]
    }
).to_dataframe()
print("Global Model Residuals")

Global Model Residuals


The ‘Year’ feature jumps out in the above comparison – in the global residual the MAE was approximately 2, but in the localized region the MAE is much higher.

This is perhaps not a big surprise considering the cases we chose to investigate (Kia K900) which was a luxury car, which generally will have less variation year over year hence the ‘Year’ feature is more difficult to predict accurately.


## Step 5: Further Inspection of Anomalous Cases

We identified some anomalous cases earlier and displayed them, but we didn't do much in the way of qualifying their anomalous nature. One good way to do this, is to view the most similar and boundary cases of the anomalous cases. 

Below we define a helper method that will help us extract and display this information conveniently for a given case (it's session id and training index, which are used as a pair to specify cases in the Howso Engine).

In [41]:
# Helper function to extract out most similar and boundary cases
def get_info(case):
    details = {'most_similar_cases': True,
               'num_most_similar_cases': 10,
               'boundary_cases': True,
               'num_boundary_cases': 10,
               'influential_cases': True}

    new_result = t.react(case_indices=case, preserve_feature_values=context_features, leave_case_out=True,
                         details=details, action_features=action_features)

    print('')
    most_similar_df = new_result['details']['influential_cases'][0].drop('VehicleClass', axis=1)

    most_similar_records = pd.merge(most_similar_df, df_original, on=context_features, how='left')

    cols_order = ['.influence_weight', '.session', '.session_training_index', 'Make', 'Model', 'Year'] + most_similar_records.columns.drop(['.session_training_index', '.session', '.influence_weight', 'Make', 'Model', 'Year']).tolist()

    most_similar_records = most_similar_records.loc[ : , cols_order]

    print('Similar cases:')
    display(most_similar_records)

    boundary_case_df = new_result['details']['boundary_cases'][0].drop('VehicleClass', axis=1)

    boundary_records = pd.merge(boundary_case_df, df_original, on=context_features, how='inner')

    cols_order = ['.influence_weight', '.session', '.session_training_index', 'Make', 'Model', 'Year'] + boundary_records.columns.drop(['.session_training_index',  '.session', '.influence_weight', 'Make', 'Model', 'Year']).tolist()

    boundary_records = boundary_records.loc[ : , cols_order]
    print('Boundary cases:')
    display(boundary_records)

In [37]:
# Pick the lowest and highest conviction cases
low_convict_record = convict_df.sort_values('convictions', ascending=True).iloc[0, :]
low_convict_case_index = [(low_convict_record['.session'], low_convict_record['.session_training_index'])]

high_convict_record = convict_df.sort_values('convictions', ascending=False).iloc[0, :]
high_convict_case_index = [(high_convict_record['.session'], high_convict_record['.session_training_index'])]

In [38]:
# Lowest conviction record
low_convict_record

CityMPG                                                      13
DriveType                                      Rear-Wheel Drive
FuelType                                                Regular
HighwayMPG                                                   17
Make                                              Federal Coach
Model                                                       85J
Year                                                       1995
PassengerVolume                                             176
LuggageVolume                                                 1
VehicleClass                                         Large Cars
convictions                                            0.006235
.session_training_index                                    1085
.session                   4256ce17-56fc-418b-9980-8146c8751a64
Name: 1085, dtype: object

In [42]:
# View its similar and boundary cases
get_info(low_convict_case_index)


Similar cases:


.influence_weight                              .session  \
0           0.432715  4256ce17-56fc-418b-9980-8146c8751a64   
1           0.408661  4256ce17-56fc-418b-9980-8146c8751a64   
2           0.065836  4256ce17-56fc-418b-9980-8146c8751a64   
3           0.050931  4256ce17-56fc-418b-9980-8146c8751a64   
4           0.041858  4256ce17-56fc-418b-9980-8146c8751a64   

   .session_training_index        Make                        Model  Year  \
0                    18684     Ferrari        3.2 Mondial/Cabriolet  1989   
1                      801  Mitsubishi               3000 GT Spyder  1995   
2                      802  Mitsubishi               3000 GT Spyder  1995   
3                    17452     Ferrari        3.2 Mondial/Cabriolet  1988   
4                      268     Ferrari  Ferrari Mondial T/Cabriolet  1994   

   LuggageVolume                   DriveType FuelType  PassengerVolume  \
0              3            Rear-Wheel Drive  Regular               76   
1              4           Front-Wheel Drive  Regular               84   
2              4  4-Wheel or All-Wheel Drive  Premium               84   
3              3            Rear-Wheel Drive  Regular               76   
4              4            Rear-Wheel Drive  Premium               81   

   CityMPG  HighwayMPG      VehicleClass  
0       11          17  Minicompact Cars  
1       16          22   Subcompact Cars  
2       15          22   Subcompact Cars  
3       11          17  Minicompact Cars  
4       11          16   Subcompact Cars

Boundary cases:


.influence_weight                              .session  \
0                  0  4256ce17-56fc-418b-9980-8146c8751a64   
1                  0  4256ce17-56fc-418b-9980-8146c8751a64   
2                  0  4256ce17-56fc-418b-9980-8146c8751a64   
3                  0  4256ce17-56fc-418b-9980-8146c8751a64   
4                  0  4256ce17-56fc-418b-9980-8146c8751a64   
5                  0  4256ce17-56fc-418b-9980-8146c8751a64   
6                  0  4256ce17-56fc-418b-9980-8146c8751a64   
7                  0  4256ce17-56fc-418b-9980-8146c8751a64   
8                  0  4256ce17-56fc-418b-9980-8146c8751a64   
9                  0  4256ce17-56fc-418b-9980-8146c8751a64   

   .session_training_index                           Make  \
0                     1080                  Federal Coach   
1                     1082                  Federal Coach   
2                     1083                  Federal Coach   
3                     1086                  Federal Coach   
4                     1088                  Federal Coach   
5                     1090                  Federal Coach   
6                     5154         Bitter Gmbh and Co. Kg   
7                     9194  Bill Dovell Motor Car Company   
8                    11330         Bitter Gmbh and Co. Kg   
9                    11340         Bitter Gmbh and Co. Kg   

                   Model  Year  LuggageVolume         DriveType FuelType  \
0                  Eagle  1995             13  Rear-Wheel Drive  Regular   
1               Six Door  1995             20  Rear-Wheel Drive  Regular   
2                Windsor  1995             13  Rear-Wheel Drive  Regular   
3  Lincoln Eagle/Windsor  1995             17  Rear-Wheel Drive  Regular   
4           Lincoln 100J  1995             17  Rear-Wheel Drive  Regular   
5            Lincoln 85J  1995             17  Rear-Wheel Drive  Regular   
6              Bitter SC  1986             13  Rear-Wheel Drive  Premium   
7            Dovell 230E  1984             13              None  Regular   
8              Bitter SC  1987             13  Rear-Wheel Drive  Regular   
9              Bitter SC  1987             13  Rear-Wheel Drive  Premium   

   PassengerVolume  CityMPG  HighwayMPG  VehicleClass  
0              149       13          17    Large Cars  
1              154       13          17    Large Cars  
2              147       13          17    Large Cars  
3              157       14          20    Large Cars  
4              192       14          20    Large Cars  
5              187       14          20    Large Cars  
6              194       14          20  Compact Cars  
7              189       17          19  Compact Cars  
8              194       14          17  Compact Cars  
9              194       14          20  Compact Cars

We see that our lowest conviction record is an electric car. This is fairly unsurprising, at this is definitely not a common type of car, especially for the period of time that this dataset represents. We additionally see that almost all of the ".influence_weight" is in a single one of its similar cases. This makes up for a large part of it's low Familiarity Conviction.

Additionally, looking at the Boundary Cases, we see many other cars that are also electric, but most have more luggage volume or better highway milage. Not to mention that they are also distinctly different from the anomalous case as they are not a Subcompact car.

In [43]:
# Highest conviction record
high_convict_record

CityMPG                                                      21
DriveType                                     Front-Wheel Drive
FuelType                                                Regular
HighwayMPG                                                   32
Make                                                 Oldsmobile
Model                                                   Achieva
Year                                                       1994
PassengerVolume                                              90
LuggageVolume                                                14
VehicleClass                                       Compact Cars
convictions                                         1214.588928
.session_training_index                                     470
.session                   4256ce17-56fc-418b-9980-8146c8751a64
Name: 470, dtype: object

In [44]:
# View its similar and boundary cases
get_info(high_convict_case_index)


Similar cases:


.influence_weight                              .session  \
0           0.225490  4256ce17-56fc-418b-9980-8146c8751a64   
1           0.223581  4256ce17-56fc-418b-9980-8146c8751a64   
2           0.195999  4256ce17-56fc-418b-9980-8146c8751a64   
3           0.176819  4256ce17-56fc-418b-9980-8146c8751a64   
4           0.116893  4256ce17-56fc-418b-9980-8146c8751a64   
5           0.061218  4256ce17-56fc-418b-9980-8146c8751a64   

   .session_training_index        Make    Model  Year  LuggageVolume  \
0                    21399  Oldsmobile  Achieva  1993             14   
1                      436    Infiniti      G20  1994             14   
2                      489      Subaru   Legacy  1994             14   
3                      468  Oldsmobile  Achieva  1994             14   
4                    21330   Chevrolet  Beretta  1993             14   
5                      469  Oldsmobile  Achieva  1994             14   

           DriveType FuelType  PassengerVolume  CityMPG  HighwayMPG  \
0  Front-Wheel Drive  Regular               90       21          32   
1  Front-Wheel Drive  Regular               89       21          29   
2  Front-Wheel Drive  Regular               90       20          28   
3  Front-Wheel Drive  Regular               90       19          29   
4  Front-Wheel Drive  Regular               90       22          31   
5  Front-Wheel Drive  Regular               90       18          28   

   VehicleClass  
0  Compact Cars  
1  Compact Cars  
2  Compact Cars  
3  Compact Cars  
4  Compact Cars  
5  Compact Cars

Boundary cases:


.influence_weight                              .session  \
0                   0  4256ce17-56fc-418b-9980-8146c8751a64   
1                   0  4256ce17-56fc-418b-9980-8146c8751a64   
2                   0  4256ce17-56fc-418b-9980-8146c8751a64   
3                   0  4256ce17-56fc-418b-9980-8146c8751a64   
4                   0  4256ce17-56fc-418b-9980-8146c8751a64   
5                   0  4256ce17-56fc-418b-9980-8146c8751a64   
6                   0  4256ce17-56fc-418b-9980-8146c8751a64   
7                   0  4256ce17-56fc-418b-9980-8146c8751a64   
8                   0  4256ce17-56fc-418b-9980-8146c8751a64   
9                   0  4256ce17-56fc-418b-9980-8146c8751a64   
10                  0  4256ce17-56fc-418b-9980-8146c8751a64   

    .session_training_index       Make     Model  Year  LuggageVolume  \
0                       239  Chevrolet  Cavalier  1994             13   
1                       240  Chevrolet  Cavalier  1994             13   
2                       292    Hyundai     Excel  1994             14   
3                       292    Hyundai    Precis  1994             14   
4                       339    Pontiac   Sunbird  1994             13   
5                       340    Pontiac   Sunbird  1994             13   
6                      1292      Honda     Civic  1996             13   
7                     20729    Pontiac   Sunbird  1992             13   
8                     21154  Chevrolet  Cavalier  1993             13   
9                     21276    Pontiac   Sunbird  1993             13   
10                    21277    Pontiac   Sunbird  1993             13   

            DriveType FuelType  PassengerVolume  CityMPG  HighwayMPG  \
0   Front-Wheel Drive  Regular               88       20          30   
1   Front-Wheel Drive  Regular               88       22          33   
2   Front-Wheel Drive  Regular               86       23          32   
3   Front-Wheel Drive  Regular               86       23          32   
4   Front-Wheel Drive  Regular               89       21          29   
5   Front-Wheel Drive  Regular               89       22          32   
6   Front-Wheel Drive  Regular               90       24          32   
7   Front-Wheel Drive  Regular               88       22          32   
8   Front-Wheel Drive  Regular               88       22          33   
9   Front-Wheel Drive  Regular               89       21          29   
10  Front-Wheel Drive  Regular               89       22          32   

       VehicleClass  
0   Subcompact Cars  
1   Subcompact Cars  
2   Subcompact Cars  
3      Compact Cars  
4   Subcompact Cars  
5   Subcompact Cars  
6   Subcompact Cars  
7   Subcompact Cars  
8   Subcompact Cars  
9   Subcompact Cars  
10  Subcompact Cars

Looking at the highest conviction case, we should expect a case that is barely surprising. It has a conviction value of over 10,000, which is to say that the case is over 10,000 times less surprising than we expect from the average new case. Looking at the similar cases, it becomes obvious why this happened. Every similar case is exact same model of car with practically the *exact* same feature values except for "PassengerVolume" which is merely 1% different.

Then looking at boundary cases, we see many Rolls-Royce models that also have almost identical feature values across the board, save for "PassengerVolume" again, which is now about 5-7% different, but apparently this gives cause to classify these cars as "Compact Cars".

# Conclusion

This use-case driven demo demonstrating the interpretability and predictive power of the Howso Engine hope to serve as a strong example for Howso Engine users who have created a Trainee and want ideas or guidance on how to make predictions that they can deeply understand and investigate.